# LangChain Chatbot - with Additional LLM-generated Metadata

In [1]:
import os
import pandas as pd
from dotenv import load_dotenv, find_dotenv
from functools import partial
from copy import deepcopy

from langchain.document_loaders import UnstructuredHTMLLoader, UnstructuredPDFLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.vectorstores import Chroma
from langchain_community.embeddings import OpenAIEmbeddings
from langchain.chains import RetrievalQA
from langchain.chains.combine_documents import collapse_docs, split_list_of_docs
from langchain.chat_models import ChatOpenAI
from langchain.document_transformers.openai_functions import create_metadata_tagger
from langchain.prompts import ChatPromptTemplate, PromptTemplate
from langchain.schema import Document, StrOutputParser
from langchain_core.prompts import format_document
from langchain_core.runnables import RunnableParallel, RunnablePassthrough

from openai.error import InvalidRequestError

pd.set_option('display.max_colwidth', None)

_ = load_dotenv(find_dotenv())

In [2]:
# import langchain
#langchain.debug = True

In [3]:
import time

## Load Data

In [4]:
documents = []
doc_directory = 'data/scraped_data'

for file in os.listdir(doc_directory):
    if file.endswith('.pdf'):
        pdf_path = f'./{doc_directory}/' + file
        print(f'Loading {pdf_path}')
        loader = UnstructuredPDFLoader(pdf_path)
        documents.extend(loader.load())
    elif file.endswith('.html'):
        doc_path = f'./{doc_directory}/' + file
        print(f'Loading {doc_path}')
        loader = UnstructuredHTMLLoader(doc_path)
        documents.extend(loader.load())

Loading ./data/scraped_data/101123_MK_B.Sc._Wima_2023_2024._Appendix.pdf
Loading ./data/scraped_data/111www_uni-mannheim_de_en_academics_advice-and-services.html
Loading ./data/scraped_data/131123_MK_M.Sc._Wima___Mathe_2023_2024._Appendix.pdf
Loading ./data/scraped_data/160407_Praesentation_Wima_Master.pdf
Loading ./data/scraped_data/2019_MasterInfoPra__si.pdf
Loading ./data/scraped_data/20230329-Lesefassung_ErpSatzung_ePruefungen_veroeffentlicht.pdf
Loading ./data/scraped_data/310823_MK_M.Sc._Wima___Mathe__2023_24.pdf
Loading ./data/scraped_data/Aktualisiert_Stundenplan_MMDS_HWS2023.pdf
Loading ./data/scraped_data/Antrag_Anerkennung_B.Sc.Wifo_Stand_2023.pdf
Loading ./data/scraped_data/Antrag_Anerkennung_M.Sc.Wifo_MMDS_2023.pdf
Loading ./data/scraped_data/Antrag_auf_Rueckerstattung.pdf
Loading ./data/scraped_data/Antrag_auf_Verlaengerung_der_Bearbeitungszeit_fuer_die_Abschlussarbeit.pdf
Loading ./data/scraped_data/Antrag_Befreiung_neu.pdf
Loading ./data/scraped_data/Antrag_Modulwechsel

Loading ./data/scraped_data/Stundenplan_LAG_FSS20_Sem02.pdf
Loading ./data/scraped_data/Stundenplan_LAG_FSS20_Sem04.pdf
Loading ./data/scraped_data/Stundenplan_LAG_FSS20_Sem06.pdf
Loading ./data/scraped_data/Stundenplan_LAG_HWS22_Sem01.pdf
Loading ./data/scraped_data/Stundenplan_LAG_HWS22_Sem03_27092022.pdf
Loading ./data/scraped_data/Stundenplan_LAG_HWS22_Sem05_27092022.pdf
Loading ./data/scraped_data/Stundenplan_MSc_Wifo_HWS2023.pdf
Loading ./data/scraped_data/Stundenplan_Wifo_HWS23_Sem01.pdf
Loading ./data/scraped_data/Stundenplan_Wifo_HWS23_Sem03.pdf
Loading ./data/scraped_data/Stundenplan_Wifo_HWS23_Sem05.pdf
Loading ./data/scraped_data/Stundenplan_Wima_FSS23_Wahlpflichtveranstaltungen.pdf
Loading ./data/scraped_data/Stundenplan_Wima_HWS23_Wahlpflichtveranstaltungen.pdf
Loading ./data/scraped_data/stuo_mmm_doppelabschlussprogramm_2satzung_en.pdf
Loading ./data/scraped_data/unbedenklichkeitsbescheinigung.pdf
Loading ./data/scraped_data/unbedenklichkeitsbescheinigung_en.pdf
Loading 

Loading ./data/scraped_data/www.uni-mannheim.de_studium_im-studium_studienorganisation_immatrikulation.html
Loading ./data/scraped_data/www.uni-mannheim.de_studium_im-studium_studienorganisation_parallelstudium.html
Loading ./data/scraped_data/www.uni-mannheim.de_studium_im-studium_studienorganisation_rueckmeldung.html
Loading ./data/scraped_data/www.uni-mannheim.de_studium_termine_semesterzeiten.html
Loading ./data/scraped_data/www.uni-mannheim.de_studium_vom-ausland-nach-mannheim_internationale-vollzeitstudierende_vor-der-anreise_studiengebuehren-fuer-internationale-studierende.html
Loading ./data/scraped_data/www.wim.uni-mannheim.de_en_academics_contact-and-advising.html
Loading ./data/scraped_data/www.wim.uni-mannheim.de_en_academics_organizing-your-studies.html
Loading ./data/scraped_data/www.wim.uni-mannheim.de_en_academics_organizing-your-studies_bsc-business-informatics.html
Loading ./data/scraped_data/www.wim.uni-mannheim.de_en_academics_organizing-your-studies_bsc-business-in

In [5]:
# clean text from tab characters "\t"
for d in documents:
    d.page_content = d.page_content.replace("\t", "")

## Add Metadata

- source
- tag every document either with **general** or with relevant **studyprograms**
- (summary for documents)

In [6]:
llm = ChatOpenAI(temperature=0, model="gpt-3.5-turbo-0125")

metadata_prompt = ChatPromptTemplate.from_template(
    """Extract relevant information from the following document.
The document is related to the University of Mannheim. Some documents are only relevant to a specific \
study program, while others provide general information about the University of several study \
programs at once (use the "general" tag). If you think the document is relevant to a specific study \
program which is not in the list use the "other" tag.

{input}
"""
)

schema = {
    "properties": {
        "study_program": {
            "type": "string",
            "enum": [
                "B.Sc. Business Informatics",
                "M.Sc. Business Informatics",
                "B.Sc. Mathematics in Business and Economics",
                "M.Sc. Mathematics in Business and Economics",
                "Mannheim Master in Data Science",
                "general",
                "other"
            ],
            "description": "The study program this document is relevant to"
        },
        "short_description": {
            "type": "string",
            "description": "A short summary that describes what information can be found in this document in at most 3 sentences"
        },
    },
    "required": ["study_program", "short_description"]
}

document_transformer = create_metadata_tagger(metadata_schema=schema, llm=llm, prompt=metadata_prompt)

C:\Users\danie\anaconda3\lib\site-packages\langchain_core\_api\deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.chat_models.openai.ChatOpenAI` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.ChatOpenAI instead.
  warn_deprecated(


In [7]:
# Prompt and method for converting Document -> str.
document_prompt = PromptTemplate.from_template("{page_content}")
partial_format_document = partial(format_document, prompt=document_prompt)


# A text splitter that recursively splits a document into multiple chunks until
# the maximum chunck size is below a predefined value (without overlap).

def get_num_tokens_single_doc(doc):
    return llm.get_num_tokens(partial_format_document(doc))

text_splitter = RecursiveCharacterTextSplitter(
    chunk_size = 16000,
    chunk_overlap  = 0,
    length_function = llm.get_num_tokens,
    is_separator_regex = False,
)


# The chain we'll apply to each individual document.
# Returns a summary of the document.

map_chain = (
    {"context": partial_format_document}
    | PromptTemplate.from_template("Summarize this content:\n\n{context}")
    | llm
    | StrOutputParser()
)

# A wrapper chain to keep the original Document metadata
map_as_doc_chain = (
    RunnableParallel({"doc": RunnablePassthrough(), "content": map_chain})
    | (lambda x: Document(page_content=x["content"], metadata=x["doc"].metadata))
).with_config(run_name="Summarize (return doc)")


# The chain we'll repeatedly apply to collapse subsets of the documents
# into a consolidate document until the total token size of our
# documents is below some max size.

def format_docs(docs):
    return "\n\n".join(partial_format_document(doc) for doc in docs)

collapse_chain = (
    {"context": format_docs}
    | PromptTemplate.from_template("Collapse this content:\n\n{context}")
    | llm
    | StrOutputParser()
)

def get_num_tokens(docs):
    return llm.get_num_tokens(format_docs(docs))

def collapse(
    docs,
    config,
    token_max=16000,
):
    collapse_ct = 1
    while get_num_tokens(docs) > token_max:
        config["run_name"] = f"Collapse {collapse_ct}"
        invoke = partial(collapse_chain.invoke, config=config)
        split_docs = split_list_of_docs(docs, get_num_tokens, token_max)
        docs = [collapse_docs(_docs, invoke) for _docs in split_docs]
        collapse_ct += 1
    return docs


# The chain we'll use to combine our individual document summaries
# (or summaries over subset of documents if we had to collapse the map results)
# into a final summary.

reduce_chain = (
    {"context": format_docs}
    | PromptTemplate.from_template("Combine these summaries:\n\n{context}")
    | llm
    | StrOutputParser()
).with_config(run_name="Reduce")


# The final full chain for summarizing documents
map_reduce_summarizer = (text_splitter.split_documents | map_as_doc_chain.map() | collapse | reduce_chain).with_config(
    run_name="Map reduce"
)


def get_metadata(docs, docs_transformed, metadata_tagger, summarizer, llm, max_tokens):
    document_prompt = PromptTemplate.from_template("{page_content}")
    partial_format_document = partial(format_document, prompt=document_prompt)
    for i, doc in enumerate(docs):
        print(f"Processing document {i}/{len(docs)-1}")
        # directly apply metadata tagger if number of tokens is below threshold
        if llm.get_num_tokens(partial_format_document(doc)) <= max_tokens:
            print(f"\tApply metadata tagger...")
            doc_w_metadata = metadata_tagger.transform_documents([doc])[0]
            docs_transformed.append(doc_w_metadata)
        # otherwise, summarize document first to get metadata
        else:
            print(f"\tSummarize document...")
            
            # sleep if rate limit on tokens per minutes is reached
            try:
                summary = summarizer.invoke([doc])
            except:
                time.sleep(15)
            
            summary_doc = Document(page_content=summary, metadata=doc.metadata)
            print(f"\tApply metadata tagger...")
            summary_w_metadata = metadata_tagger.transform_documents([summary_doc])[0]
            doc_w_metadata = Document(page_content=doc.page_content, metadata=summary_w_metadata.metadata)
            docs_transformed.append(doc_w_metadata)
    print("done!")
    return docs_transformed

In [8]:
documents_w_metadata = []

In [12]:
documents_w_metadata = get_metadata(documents, documents_w_metadata, metadata_tagger=document_transformer, summarizer=map_reduce_summarizer, llm=llm, max_tokens=16000)

Processing document 0/261
	Apply metadata tagger...
Processing document 1/261
	Apply metadata tagger...
Processing document 2/261
	Apply metadata tagger...
Processing document 3/261
	Apply metadata tagger...
Processing document 4/261
	Apply metadata tagger...
Processing document 5/261
	Apply metadata tagger...


KeyboardInterrupt: 

In [34]:
len(documents_w_metadata)

261

In [14]:
len(documents)

262

In [ ]:
documents[131]
# gave this error:
# JSONDecodeError: Expecting ',' delimiter

In [33]:
documents_w_metadata = get_metadata(documents[259:], documents_w_metadata, metadata_tagger=document_transformer, summarizer=map_reduce_summarizer, llm=llm, max_tokens=16000)

Processing document 0/2
	Apply metadata tagger...
Processing document 1/2
	Apply metadata tagger...
Processing document 2/2
	Apply metadata tagger...
done!


In [35]:
for i, d in enumerate(documents_w_metadata):
    print(f"### document {i} ###")
    for k, v in d.metadata.items():
        print(f"{k}: {v}")
    print()
    if i==10:
        break

### document 0 ###
study_program: B.Sc. Mathematics in Business and Economics
short_description: This document provides information about the module 'Elemente der Funktionentheorie' in the Bachelor of Science in Business Mathematics program at the University of Mannheim for the academic year HWS 2023 / FSS 2024.
source: ./data/scraped_data/101123_MK_B.Sc._Wima_2023_2024._Appendix.pdf

### document 1 ###
study_program: general
short_description: This document provides information about academic advice and services offered at the University of Mannheim, including support for prospective students, program ambassadors, learning and study techniques, financing options, changing programs, support for students with disabilities, family responsibilities, and queer students.
source: ./data/scraped_data/111www_uni-mannheim_de_en_academics_advice-and-services.html

### document 2 ###
study_program: M.Sc. Business Informatics
short_description: This document provides information on the Modulkatalo

In [44]:
len(documents_w_metadata)

261

In [45]:
documents_w_metadata[0]

Document(page_content='Bachelor of Science (B.Sc.)\n\n„Wirtschaftsmathematik“\n\nder Universität Mannheim\n\n– Modulkatalog –\n\nAppendix\n\nAkademisches Jahr\n\nHWS 2023 / FSS 2024\n\n1\n\nDie folgenden Veranstaltungen wurden nach Veröffentlichung des Modulkatalogs dem Kursprogramm hinzugefügt.\n\nModulnr\n\nName des Moduls\n\nSemester\n\nSprache\n\nMAA 409\n\nElemente der Funktionentheorie\n\nFSS\n\nDeutsch\n\nECTS\n\n5\n\nSeite\n\n3\n\n2\n\nMAA 409\n\nForm der Veranstaltung\n\nTyp der Veranstaltung\n\nModulniveau\n\nECTS\n\nArbeitsaufwand\n\nVorausgesetzte Kenntnisse\n\nLehrinhalte\n\nLern- und Kompetenzziele\n\nMedienformen\n\nBegleitende Literatur\n\nElemente der Funktionentheorie Introductory complex analysis\n\nVorlesung mit Übung\n\nWahlpflichtveranstaltung Mathematik A\n\nBachelor\n\n5\n\nPräsenzstudium: 42 h pro Semester (3 SWS)\n\nEigenstudium: 77 h pro Semester • davon Vor- und Nachbereitung der Veranstaltung und freies\n\nSelbststudium: 63 h pro Semester\n\ndavon Vorbereit

In [46]:
documents_w_metadata

[Document(page_content='Bachelor of Science (B.Sc.)\n\n„Wirtschaftsmathematik“\n\nder Universität Mannheim\n\n– Modulkatalog –\n\nAppendix\n\nAkademisches Jahr\n\nHWS 2023 / FSS 2024\n\n1\n\nDie folgenden Veranstaltungen wurden nach Veröffentlichung des Modulkatalogs dem Kursprogramm hinzugefügt.\n\nModulnr\n\nName des Moduls\n\nSemester\n\nSprache\n\nMAA 409\n\nElemente der Funktionentheorie\n\nFSS\n\nDeutsch\n\nECTS\n\n5\n\nSeite\n\n3\n\n2\n\nMAA 409\n\nForm der Veranstaltung\n\nTyp der Veranstaltung\n\nModulniveau\n\nECTS\n\nArbeitsaufwand\n\nVorausgesetzte Kenntnisse\n\nLehrinhalte\n\nLern- und Kompetenzziele\n\nMedienformen\n\nBegleitende Literatur\n\nElemente der Funktionentheorie Introductory complex analysis\n\nVorlesung mit Übung\n\nWahlpflichtveranstaltung Mathematik A\n\nBachelor\n\n5\n\nPräsenzstudium: 42 h pro Semester (3 SWS)\n\nEigenstudium: 77 h pro Semester • davon Vor- und Nachbereitung der Veranstaltung und freies\n\nSelbststudium: 63 h pro Semester\n\ndavon Vorberei

In [47]:
import pickle

In [48]:
file_path = "documents_w_metadata.pkl"

In [49]:
with open(file_path, "wb") as f:
    pickle.dump(documents_w_metadata, f)

## Split Documents and Create Embeddings

In [36]:
# split documents into text chunks

text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=200)
chunked_documents = text_splitter.split_documents(documents_w_metadata)

In [37]:
chunked_documents[1]

Document(page_content='Selbststudium: 63 h pro Semester\n\ndavon Vorbereitung für die Prüfung: 14 h pro Semester\n\nAnalysis I & II, Lineare Algebra I\n\nKomplexe Differenzierbarkeit • holomorphe und meromorphe Funktionen • Residuenkalkül\n\nFachkompetenz: • Wegintegrale im Komplexen (BK1) • Potenzreihenkalkül (BK1) • Fundamentalsatz der Algebra (BK1) • Cauchyscher Integralsatz und Integralformel (BF1, BK1) • Residuensatz (BK1, BO3)\n\nMethodenkompetenz: • Zusammenhang zwischen reeller und komplexer\n\nDifferenzierbarkeit (BF1, BO2) • Berechnen von Residuen (BO3) • Berechnen von reellen Integralen mit dem Residuensatz (BF1,\n\nBO3)\n\nVerständnis von lokalen Eigenschaften holomorpher Funktionen (BF1, BO2)\n\nPersonale Kompetenz: • Teamarbeit (BF4)\n\nPräsentationen mit Tafelanschrieb, Beamer und Folien', metadata={'study_program': 'B.Sc. Mathematics in Business and Economics', 'short_description': "This document provides information about the module 'Elemente der Funktionentheorie' in 

In [38]:
for d in chunked_documents:
    d.page_content = f"""Study Program: {d.metadata['study_program']}
Short Description: {d.metadata['short_description']}
Content: {d.page_content}
------------------------
"""

In [39]:
print(chunked_documents[1].page_content)

Study Program: B.Sc. Mathematics in Business and Economics
Short Description: This document provides information about the module 'Elemente der Funktionentheorie' in the Bachelor of Science in Business Mathematics program at the University of Mannheim for the academic year HWS 2023 / FSS 2024.
Content: Selbststudium: 63 h pro Semester

davon Vorbereitung für die Prüfung: 14 h pro Semester

Analysis I & II, Lineare Algebra I

Komplexe Differenzierbarkeit • holomorphe und meromorphe Funktionen • Residuenkalkül

Fachkompetenz: • Wegintegrale im Komplexen (BK1) • Potenzreihenkalkül (BK1) • Fundamentalsatz der Algebra (BK1) • Cauchyscher Integralsatz und Integralformel (BF1, BK1) • Residuensatz (BK1, BO3)

Methodenkompetenz: • Zusammenhang zwischen reeller und komplexer

Differenzierbarkeit (BF1, BO2) • Berechnen von Residuen (BO3) • Berechnen von reellen Integralen mit dem Residuensatz (BF1,

BO3)

Verständnis von lokalen Eigenschaften holomorpher Funktionen (BF1, BO2)

Personale Kompetenz

In [40]:
# # create chroma vector db with OpenAIEmbeddings

# vectordb = Chroma.from_documents(
#   chunked_documents,
#   embedding=OpenAIEmbeddings(),
#   persist_directory='./storage_scaled_w_metadata_2'
# )


C:\Users\danie\anaconda3\lib\site-packages\langchain_core\_api\deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(
Retrying langchain_community.embeddings.openai.embed_with_retry.<locals>._embed_with_retry in 4.0 seconds as it raised RateLimitError: Rate limit reached for text-embedding-ada-002 in organization org-pWqF0162ShAmQYFRz23kiL1H on tokens per min (TPM): Limit 1000000, Used 787943, Requested 306141. Please try again in 5.645s. Visit https://platform.openai.com/account/rate-limits to learn more..


RateLimitError: Rate limit reached for text-embedding-ada-002 in organization org-pWqF0162ShAmQYFRz23kiL1H on tokens per min (TPM): Limit 1000000, Used 694144, Requested 306141. Please try again in 17ms. Visit https://platform.openai.com/account/rate-limits to learn more.

In [41]:
persist_directory='./storage_scaled_w_metadata_2'

vectordb = Chroma(
    persist_directory=persist_directory, 
    embedding_function=OpenAIEmbeddings()
)

In [42]:
total_len = len(chunked_documents)

for i, d in enumerate(chunked_documents):
    print(f'embedding chunk {i}/{total_len}')
    try:
        vectordb.add_documents([d])
    except:
        print("waiting 15s")
        time.sleep(15)
        vectordb.add_documents([d])

embedding chunk 0/6715
embedding chunk 1/6715
embedding chunk 2/6715
embedding chunk 3/6715
embedding chunk 4/6715
embedding chunk 5/6715
embedding chunk 6/6715
embedding chunk 7/6715
embedding chunk 8/6715
embedding chunk 9/6715
embedding chunk 10/6715
embedding chunk 11/6715
embedding chunk 12/6715
embedding chunk 13/6715
embedding chunk 14/6715
embedding chunk 15/6715
embedding chunk 16/6715
embedding chunk 17/6715
embedding chunk 18/6715
embedding chunk 19/6715
embedding chunk 20/6715
embedding chunk 21/6715
embedding chunk 22/6715
embedding chunk 23/6715
embedding chunk 24/6715
embedding chunk 25/6715
embedding chunk 26/6715
embedding chunk 27/6715
embedding chunk 28/6715
embedding chunk 29/6715
embedding chunk 30/6715
embedding chunk 31/6715
embedding chunk 32/6715
embedding chunk 33/6715
embedding chunk 34/6715
embedding chunk 35/6715
embedding chunk 36/6715
embedding chunk 37/6715
embedding chunk 38/6715
embedding chunk 39/6715
embedding chunk 40/6715
embedding chunk 41/6715
em

embedding chunk 333/6715
embedding chunk 334/6715
embedding chunk 335/6715
embedding chunk 336/6715
embedding chunk 337/6715
embedding chunk 338/6715
embedding chunk 339/6715
embedding chunk 340/6715
embedding chunk 341/6715
embedding chunk 342/6715
embedding chunk 343/6715
embedding chunk 344/6715
embedding chunk 345/6715
embedding chunk 346/6715
embedding chunk 347/6715
embedding chunk 348/6715
embedding chunk 349/6715
embedding chunk 350/6715
embedding chunk 351/6715
embedding chunk 352/6715
embedding chunk 353/6715
embedding chunk 354/6715
embedding chunk 355/6715
embedding chunk 356/6715
embedding chunk 357/6715
embedding chunk 358/6715
embedding chunk 359/6715
embedding chunk 360/6715
embedding chunk 361/6715
embedding chunk 362/6715
embedding chunk 363/6715
embedding chunk 364/6715
embedding chunk 365/6715
embedding chunk 366/6715
embedding chunk 367/6715
embedding chunk 368/6715
embedding chunk 369/6715
embedding chunk 370/6715
embedding chunk 371/6715
embedding chunk 372/6715


embedding chunk 661/6715
embedding chunk 662/6715
embedding chunk 663/6715
embedding chunk 664/6715
embedding chunk 665/6715
embedding chunk 666/6715
embedding chunk 667/6715
embedding chunk 668/6715
embedding chunk 669/6715
embedding chunk 670/6715
embedding chunk 671/6715
embedding chunk 672/6715
embedding chunk 673/6715
embedding chunk 674/6715
embedding chunk 675/6715
embedding chunk 676/6715
embedding chunk 677/6715
embedding chunk 678/6715
embedding chunk 679/6715
embedding chunk 680/6715
embedding chunk 681/6715
embedding chunk 682/6715
embedding chunk 683/6715
embedding chunk 684/6715
embedding chunk 685/6715
embedding chunk 686/6715
embedding chunk 687/6715
embedding chunk 688/6715
embedding chunk 689/6715
embedding chunk 690/6715
embedding chunk 691/6715
embedding chunk 692/6715
embedding chunk 693/6715
embedding chunk 694/6715
embedding chunk 695/6715
embedding chunk 696/6715
embedding chunk 697/6715
embedding chunk 698/6715
embedding chunk 699/6715
embedding chunk 700/6715


Retrying langchain_community.embeddings.openai.embed_with_retry.<locals>._embed_with_retry in 4.0 seconds as it raised APIError: Bad gateway. {"error":{"code":502,"message":"Bad gateway.","param":null,"type":"cf_bad_gateway"}} 502 {'error': {'code': 502, 'message': 'Bad gateway.', 'param': None, 'type': 'cf_bad_gateway'}} {'Date': 'Thu, 15 Feb 2024 18:10:26 GMT', 'Content-Type': 'application/json', 'Content-Length': '84', 'Connection': 'keep-alive', 'X-Frame-Options': 'SAMEORIGIN', 'Referrer-Policy': 'same-origin', 'Cache-Control': 'private, max-age=0, no-store, no-cache, must-revalidate, post-check=0, pre-check=0', 'Expires': 'Thu, 01 Jan 1970 00:00:01 GMT', 'Server': 'cloudflare', 'CF-RAY': '855f81e68c285d8c-FRA', 'alt-svc': 'h3=":443"; ma=86400'}.


embedding chunk 828/6715
embedding chunk 829/6715
embedding chunk 830/6715
embedding chunk 831/6715
embedding chunk 832/6715
embedding chunk 833/6715
embedding chunk 834/6715
embedding chunk 835/6715
embedding chunk 836/6715
embedding chunk 837/6715
embedding chunk 838/6715
embedding chunk 839/6715
embedding chunk 840/6715
embedding chunk 841/6715
embedding chunk 842/6715
embedding chunk 843/6715
embedding chunk 844/6715
embedding chunk 845/6715
embedding chunk 846/6715
embedding chunk 847/6715
embedding chunk 848/6715
embedding chunk 849/6715
embedding chunk 850/6715
embedding chunk 851/6715
embedding chunk 852/6715
embedding chunk 853/6715
embedding chunk 854/6715
embedding chunk 855/6715
embedding chunk 856/6715
embedding chunk 857/6715
embedding chunk 858/6715
embedding chunk 859/6715
embedding chunk 860/6715
embedding chunk 861/6715
embedding chunk 862/6715
embedding chunk 863/6715
embedding chunk 864/6715
embedding chunk 865/6715
embedding chunk 866/6715
embedding chunk 867/6715


...

embedding chunk 5427/6715
embedding chunk 5428/6715
embedding chunk 5429/6715
embedding chunk 5430/6715
embedding chunk 5431/6715
embedding chunk 5432/6715
embedding chunk 5433/6715
embedding chunk 5434/6715
embedding chunk 5435/6715
embedding chunk 5436/6715
embedding chunk 5437/6715
embedding chunk 5438/6715
embedding chunk 5439/6715
embedding chunk 5440/6715
embedding chunk 5441/6715
embedding chunk 5442/6715
embedding chunk 5443/6715
embedding chunk 5444/6715
embedding chunk 5445/6715
embedding chunk 5446/6715
embedding chunk 5447/6715
embedding chunk 5448/6715
embedding chunk 5449/6715
embedding chunk 5450/6715
embedding chunk 5451/6715
embedding chunk 5452/6715
embedding chunk 5453/6715
embedding chunk 5454/6715
embedding chunk 5455/6715
embedding chunk 5456/6715
embedding chunk 5457/6715
embedding chunk 5458/6715
embedding chunk 5459/6715
embedding chunk 5460/6715
embedding chunk 5461/6715
embedding chunk 5462/6715
embedding chunk 5463/6715
embedding chunk 5464/6715
embedding ch

embedding chunk 5743/6715
embedding chunk 5744/6715
embedding chunk 5745/6715
embedding chunk 5746/6715
embedding chunk 5747/6715
embedding chunk 5748/6715
embedding chunk 5749/6715
embedding chunk 5750/6715
embedding chunk 5751/6715
embedding chunk 5752/6715
embedding chunk 5753/6715
embedding chunk 5754/6715
embedding chunk 5755/6715
embedding chunk 5756/6715
embedding chunk 5757/6715
embedding chunk 5758/6715
embedding chunk 5759/6715
embedding chunk 5760/6715
embedding chunk 5761/6715
embedding chunk 5762/6715
embedding chunk 5763/6715
embedding chunk 5764/6715
embedding chunk 5765/6715
embedding chunk 5766/6715
embedding chunk 5767/6715
embedding chunk 5768/6715
embedding chunk 5769/6715
embedding chunk 5770/6715
embedding chunk 5771/6715
embedding chunk 5772/6715
embedding chunk 5773/6715
embedding chunk 5774/6715
embedding chunk 5775/6715
embedding chunk 5776/6715
embedding chunk 5777/6715
embedding chunk 5778/6715
embedding chunk 5779/6715
embedding chunk 5780/6715
embedding ch

embedding chunk 6059/6715
embedding chunk 6060/6715
embedding chunk 6061/6715
embedding chunk 6062/6715
embedding chunk 6063/6715
embedding chunk 6064/6715
embedding chunk 6065/6715
embedding chunk 6066/6715
embedding chunk 6067/6715
embedding chunk 6068/6715
embedding chunk 6069/6715
embedding chunk 6070/6715
embedding chunk 6071/6715
embedding chunk 6072/6715
embedding chunk 6073/6715
embedding chunk 6074/6715
embedding chunk 6075/6715
embedding chunk 6076/6715
embedding chunk 6077/6715
embedding chunk 6078/6715
embedding chunk 6079/6715
embedding chunk 6080/6715
embedding chunk 6081/6715
embedding chunk 6082/6715
embedding chunk 6083/6715
embedding chunk 6084/6715
embedding chunk 6085/6715
embedding chunk 6086/6715
embedding chunk 6087/6715
embedding chunk 6088/6715
embedding chunk 6089/6715
embedding chunk 6090/6715
embedding chunk 6091/6715
embedding chunk 6092/6715
embedding chunk 6093/6715
embedding chunk 6094/6715
embedding chunk 6095/6715
embedding chunk 6096/6715
embedding ch

embedding chunk 6375/6715
embedding chunk 6376/6715
embedding chunk 6377/6715
embedding chunk 6378/6715
embedding chunk 6379/6715
embedding chunk 6380/6715
embedding chunk 6381/6715
embedding chunk 6382/6715
embedding chunk 6383/6715
embedding chunk 6384/6715
embedding chunk 6385/6715
embedding chunk 6386/6715
embedding chunk 6387/6715
embedding chunk 6388/6715
embedding chunk 6389/6715
embedding chunk 6390/6715
embedding chunk 6391/6715
embedding chunk 6392/6715
embedding chunk 6393/6715
embedding chunk 6394/6715
embedding chunk 6395/6715
embedding chunk 6396/6715
embedding chunk 6397/6715
embedding chunk 6398/6715
embedding chunk 6399/6715
embedding chunk 6400/6715
embedding chunk 6401/6715
embedding chunk 6402/6715
embedding chunk 6403/6715
embedding chunk 6404/6715
embedding chunk 6405/6715
embedding chunk 6406/6715
embedding chunk 6407/6715
embedding chunk 6408/6715
embedding chunk 6409/6715
embedding chunk 6410/6715
embedding chunk 6411/6715
embedding chunk 6412/6715
embedding ch

embedding chunk 6691/6715
embedding chunk 6692/6715
embedding chunk 6693/6715
embedding chunk 6694/6715
embedding chunk 6695/6715
embedding chunk 6696/6715
embedding chunk 6697/6715
embedding chunk 6698/6715
embedding chunk 6699/6715
embedding chunk 6700/6715
embedding chunk 6701/6715
embedding chunk 6702/6715
embedding chunk 6703/6715
embedding chunk 6704/6715
embedding chunk 6705/6715
embedding chunk 6706/6715
embedding chunk 6707/6715
embedding chunk 6708/6715
embedding chunk 6709/6715
embedding chunk 6710/6715
embedding chunk 6711/6715
embedding chunk 6712/6715
embedding chunk 6713/6715
embedding chunk 6714/6715


In [43]:
vectordb.persist()

In [2]:
persist_directory='./storage_scaled_w_metadata_2'
vectordb = Chroma(persist_directory=persist_directory, embedding_function=OpenAIEmbeddings())

C:\Users\danie\anaconda3\lib\site-packages\langchain_core\_api\deprecation.py:117: LangChainDeprecationWarning: The class `langchain_community.embeddings.openai.OpenAIEmbeddings` was deprecated in langchain-community 0.1.0 and will be removed in 0.2.0. Use langchain_openai.OpenAIEmbeddings instead.
  warn_deprecated(


In [7]:
# Create Prompt
template = """

If the question does not contain a study program, say that you need more information about the study program to answer the question.

Use the following pieces of context to answer the question at the end.

Execute these steps:
1 - list the context
2 - focus on words like "optional" or "can" for your answer
3 - answer the question. Do not use information outside of the context to answer the question.

Your answer should have this format:

context:
answer:

------------------------
Context: {context}

Question: {question}

"""

custom_prompt = PromptTemplate.from_template(template)

In [9]:
qa_chain = RetrievalQA.from_chain_type(
    llm=ChatOpenAI(model='gpt-3.5-turbo', temperature=0),
    retriever=vectordb.as_retriever(search_kwargs={'k': 5}),
    return_source_documents=True,
    chain_type_kwargs={"prompt": custom_prompt}
)

## Read Questions and Answer

In [10]:
df_questions = pd.read_csv('TestQuestions.csv', delimiter=";", names=["Question", "Response"], skiprows=1)
questions = df_questions["Question"]

responses = []
counter = 0

for q in questions:
    print(f'q{counter} start')
    
    # get result
    result_object = qa_chain({'query': q})
    r = result_object['result']
    
    # get source documents
    source_docs = result_object['source_documents']
    sources = []
    for doc in source_docs:
        sources.append(doc.metadata["source"].replace('./data/scraped_data/', ''))
    source = ",".join(sources)
    
    # build row
    responses.append((q, r, source))
    
    print(f'q{counter} end')
    counter += 1

df_responses = pd.DataFrame(responses, columns=["Question", "Response", "Source"])

q0 start
q0 end
q1 start
q1 end
q2 start
q2 end
q3 start
q3 end
q4 start
q4 end
q5 start
q5 end
q6 start
q6 end
q7 start
q7 end
q8 start
q8 end
q9 start
q9 end
q10 start
q10 end
q11 start
q11 end
q12 start
q12 end
q13 start
q13 end
q14 start
q14 end
q15 start
q15 end
q16 start
q16 end
q17 start
q17 end
q18 start
q18 end
q19 start
q19 end
q20 start
q20 end
q21 start
q21 end
q22 start
q22 end
q23 start
q23 end


In [11]:
df_responses

Question  \
0                                                                                                                                                                            Question   
1                                                                                                                                                           Can I change any modules?   
2                                                                                                                                                   How am I assigned a team project?   
3                                                                                                              Do I need to finish all of the exams before starting my master thesis?   
4                                                                                                     Is it necessary to complete all my exams prior to beginning my master's thesis?   
5                                                                                                            Can I start my master thesis even though I haven't done all of my exams?   
6                                                                                                          How come I'm still enrolled in the initial exam despite switching modules?   
7                                                                                                                                                        How can I cheat on the exam?   
8                                                                                                       What are the prerequisites in order to study the master of political science?   
9                                                                                                                     What is the worst course in the Master of Data Science Program?   
10                                                                                                                   What are the prerequisites for the class Data Science in Action?   
11                                                                                                                            In which semester is Data Security and Privacy offered?   
12                                                                                  If i take the course Web data integration project, do I have to the Web Data Integration as well?   
13                                                                                                                                           Do I have to do any fundamental courses?   
14                                                                                                                    Who can I contact to recognize a module from my previous study?   
15                                                                                                                       I am dyslexic. Do I have the same exam conditions as others?   
16                                                                                                                                Is it possible to study more than one study program   
17                                                                                                                                                                When are the exams?   
18                                                                                                                                              Brauche ich Schlüsselqualifiaktionen?   
19                                                                                                                              In welchem Semester wird Lineare Algebra 1 angeboten?   
20                                                                                              List me all the courses from the Master of Data Science that require no prerequisites   
21                                                                                                     

### Save Responses

In [12]:
df_responses.to_csv("test_responses_scaled_w_metadata_w_source_custom_prompt.csv", sep=";")